<a href="https://colab.research.google.com/github/polyankaglade/ELTeC-eng-loc/blob/main/notebooks/Extracting_Locations.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
cd "/content/drive/MyDrive/LCT Courses/Digital Humanities/Final Project/ELTeC_locations"

/content/drive/.shortcut-targets-by-id/1roEx2vBANaiSqx40NEcB5--OhTHp8IXk/ELTeC_locations


In [ ]:
import xml.etree.ElementTree as ET
import os
import spacy
from bs4 import BeautifulSoup
from tabulate import tabulate
import pickle
import pandas as pd
from tqdm import tqdm
import time

In [ ]:
#Class Novel to structure the data for later preprocessing

class Novel:
  #Eltec_file name, , List of Paragraphs, List of paths to pargraphs
    def __init__(self, file_name, paragraphs, paragraphs_paths, locations):
      self.file_name = file_name
      self.paragraphs = paragraphs
      self.paragraphs_paths = paragraphs_paths
      self.locations = locations

    def __repr__(self):
        return f"{self.file_name}, {self.locations}"

In [ ]:
ls  ELTeC-eng-master/level1

ENG18400_Trollope.xml   ENG18700_Oliphant.xml    ENG18954_Sharp.xml
ENG18410_Sinclair.xml   ENG18702_Jenkins.xml     ENG18960_Malet.xml
ENG18411_Tupper.xml     ENG18720_Lynn.xml        ENG18961_Griffiths.xml
ENG18440_Disraeli.xml   ENG18721_Eliot.xml       ENG18970_Phillpots.xml
ENG18450_Disraeli.xml   ENG18740_Ouida.xml       ENG18972_Morris.xml
ENG18460_Reynolds.xml   ENG18741_Bulwer.xml      ENG18973_Cholmondeley.xml
ENG18470_Aguilar.xml    ENG18742_Trollope.xml    ENG18980_BaringGould.xml
ENG18471_Bronte.xml     ENG18760_Collins.xml     ENG19001_Glyn.xml
ENG18480_Thackeray.xml  ENG18770_Mallock.xml     ENG19004_Fowler.xml
ENG18481_Dickens.xml    ENG18800_Disraeli.xml    ENG19005_Steel.xml
ENG18482_Gaskell.xml    ENG18820_Anstey.xml      ENG19010_Mason.xml
ENG18490_Skene.xml      ENG18830_Broughton.xml   ENG19011_Jerome.xml
ENG18500_Ainsworth.xml  ENG18831_Ouida.xml       ENG19020_Nesbit.xml
ENG18510_Kingsley.xml   ENG18840_Lee.xml         ENG19060_Nesbit.xml
ENG18530_Dickens.xml   

In [ ]:
import os
from bs4 import BeautifulSoup

novels_dict = {}
level1_dir = './ELTeC-eng-master/level1/' # replace with the path to your directory

for novel_file in os.listdir(level1_dir):
  if os.path.isfile(os.path.join(level1_dir, novel_file)):
    print("parsing file: ", novel_file)
    with open(level1_dir+novel_file, 'r') as tei: #Opens the file
      soup = BeautifulSoup(tei, 'xml') #Parse the XML
      #chapters = soup.find_all(type="chapter")
      #for chapter in chapters:
          #p_elements = chapter.find_all('p')
      body = soup.find("We ")
      p_elements = body.find_all('p')
      paragraphs = []
      paragraphs_paths = []
      for i, p in enumerate(p_elements):
        if len(p) > 0:
          paragraphs.append(p.text)
          paragraphs_paths.append(i)
        
      novels_dict[novel_file] = Novel(novel_file,paragraphs, paragraphs_paths, [])

parsing file:  ENG18400_Trollope.xml
parsing file:  ENG18410_Sinclair.xml
parsing file:  ENG18411_Tupper.xml
parsing file:  ENG18440_Disraeli.xml
parsing file:  ENG18450_Disraeli.xml
parsing file:  ENG18460_Reynolds.xml
parsing file:  ENG18470_Aguilar.xml
parsing file:  ENG18471_Bronte.xml
parsing file:  ENG18480_Thackeray.xml
parsing file:  ENG18481_Dickens.xml
parsing file:  ENG18490_Skene.xml
parsing file:  ENG18510_Kingsley.xml
parsing file:  ENG18482_Gaskell.xml
parsing file:  ENG18500_Ainsworth.xml
parsing file:  ENG18530_Dickens.xml
parsing file:  ENG18540_Dickens.xml
parsing file:  ENG18531_Yonge.xml
parsing file:  ENG18551_Trollope.xml
parsing file:  ENG18552_Kavanagh.xml
parsing file:  ENG18560_Yonge.xml
parsing file:  ENG18570_Bronte.xml
parsing file:  ENG18600_Clive.xml
parsing file:  ENG18610_Eliot.xml
parsing file:  ENG18621_Braddon.xml
parsing file:  ENG18630_Craik.xml
parsing file:  ENG18632_Reade.xml
parsing file:  ENG18641_Stretton.xml
parsing file:  ENG18650_Trollope

In [ ]:
files_length = {}
for key, novel_obj in novels_dict.items():
  files_length[key] = len(novel_obj.paragraphs)

  

for k,v in sorted(files_length.items(), key=lambda p:p[1]):
  print(k,v)

ENG18850_Rutherford.xml 106
ENG19201_Arlen.xml 201
ENG18872_Lyall.xml 302
ENG18952_Wells.xml 306
ENG18490_Skene.xml 348
ENG18910_Yeats.xml 395
ENG18720_Lynn.xml 412
ENG18702_Jenkins.xml 419
ENG19070_Machen.xml 438
ENG19181_West.xml 450
ENG19191_Hamilton.xml 507
ENG18411_Tupper.xml 509
ENG19011_Jerome.xml 547
ENG18973_Cholmondeley.xml 549
ENG18641_Stretton.xml 551
ENG18951_Ward.xml 603
ENG18920_Grossmith.xml 623
ENG18954_Sharp.xml 684
ENG19001_Glyn.xml 697
ENG19150_Buchan.xml 708
ENG18652_Carroll.xml 753
ENG18742_Trollope.xml 784
ENG19190_Benson.xml 803
ENG18610_Eliot.xml 811
ENG18700_Oliphant.xml 829
ENG18900_Doyle.xml 829
ENG18950_Cross.xml 837
ENG18940_Dixon.xml 863
ENG19170_Conrad.xml 888
ENG18770_Mallock.xml 988
ENG18551_Trollope.xml 1029
ENG18931_Harraden.xml 1073
ENG18960_Malet.xml 1105
ENG18552_Kavanagh.xml 1133
ENG18500_Ainsworth.xml 1260
ENG19080_Chesterton.xml 1261
ENG18961_Griffiths.xml 1279
ENG18661_Oliphant.xml 1283
ENG18570_Bronte.xml 1288
ENG18740_Ouida.xml 1393
ENG18972

In [ ]:
novels_dict["ENG18850_Rutherford.xml"].paragraphs

['When I had established myself in my new lodgings in Camden Town, I found I had ten\n     pounds in my pocket, and again there was no outlook.\xa0 I examined carefully every possibility.\xa0\n     At last I remembered that a relative of mine, who held some office in the House of Commons,\n     added to his income by writing descriptive accounts of the debates, throwing in by way of\n     supplement any stray scraps of gossip which he was enabled to collect.\xa0 The rules of the House\n     as to the admission of strangers were not so strict then as they are now, and he assured me\n     that if I could but secure a commission from a newspaper, he could pass me into one of the\n     galleries, and, when there was nothing to be heard worth describing, I could remain in the\n     lobby, where I should by degrees find many opportunities of picking up intelligence which would\n     pay.\xa0 So far, so good; but how to obtain the commission?\xa0 I managed to get hold of a list of\n     all t

# Named Enity extraction

In [ ]:
class Location:
  def __init__(self, loc, loc_type, context, loc_ref):
    self.loc = loc
    self.loc_type = loc_type
    self.context = context
    self.loc_ref = loc_ref
  def __repr__(self):
    return f"{self.loc}, {self.loc_type}, {self.loc_ref}"

In [ ]:
!python -m spacy download en_core_web_lg

In [ ]:
#nlp = spacy.load('en_core_web_lg')
nlp = spacy.load("en_core_web_lg", disable=["tok2vec", "tagger", "parser", "attribute_ruler", "lemmatizer"])

In [ ]:
print(novels_dict['ENG18770_Mallock.xml'].paragraphs[4])
clean_text = re.sub('<[^<]+?>', '', str(novels_dict['ENG18770_Mallock.xml'].paragraphs[4]))
    # remove whitespace markers
clean_text = re.sub(r"[\n\t]", "", clean_text).strip()
clean_text = re.sub(' +', ' ', clean_text.strip())
print(clean_text)

 Otho Laurence inherited with his uncle’s house something of the tastes and
                        feelings of which it was the embodiment. But, though an epicure by training
                        and by temper, he had been open to other influences as well. At one time of
                        his life he had, as it is expressed by some, experienced religion; and not
                        religion only, but thought and speculation also. Indeed, ever since he was
                        twenty-four, he had been troubled by a painful sense that he ought to have
                        some mission in life. The only difficulty was that he could find none that
                        would suit him. He had considerable natural powers, and was in many ways a
                        remarkable man; but, unhappily, one of those who are remarkable because they
                        do not become famous, not because they do. He was one of those of whom it is
                        sai

In [ ]:
def print_novel_locations(novel):
  locations = []
  for location in novel.locations:
    locations.append("{}/{}".format(location.loc, location.loc_type))
  tabulate_data = [[str(novel.file_name), len(locations),  ", ".join(locations)]]

  print(tabulate(tabulate_data, headers=["File", "LOC Count", "LOCs"], tablefmt="fancy_grid"))

In [ ]:
def pickle_doc(novel_file_name, id, loc, doc):
  pickle_dir = "./locations_doc_pickle_files/{}".format(novel_file_name)
  pickle_location = "{}/{}-{}.pkl".format(pickle_dir, id, loc)
  if not os.path.exists(pickle_dir):
    # create the directory if it doesn't exist
    os.makedirs(pickle_dir)

  with open(pickle_location, 'wb') as f:
    pickle.dump(doc, f)

  print("pickle file for p_doc saved at {}".format(pickle_location))
)  return pickle_location


In [ ]:
def save_to_csv(novel):
  ##csv structure name:novel_file
  # loc, context, path, doc_path
  locations = []
  locations_type = []
  contexts = []
  loc_refs = []

  for location in novel.locations:
    locations.append(location.loc)
    locations_type.append(location.loc_type)
    contexts.append(location.context)
    loc_refs.append(location.loc_ref)

  novel_dict = {"Location": locations, "ent_type": locations_type, "context": contexts, "p_no": loc_refs}
  df = pd.DataFrame(novel_dict)

  #saving csv file in directory
  csv_dir = "./locations_csv_files"
  if not os.path.exists(csv_dir):
    # create the directory if it doesn't exist
    os.makedirs(csv_dir)

  csv_location = '{}/{}.csv'.format(csv_dir, novel.file_name)
  df.to_csv(csv_location, index=False)
  print("csv file for location saved at {}".format(csv_location))
  

In [ ]:
import re
###later pickle files

def extract_locations(novel):
  print("\nAnalyazing", novel.file_name)
  for i, p in enumerate(novel.paragraphs):
    #clean_text = p.encode("ascii", "ignore").decode()
    clean_text = re.sub('<[^<]+?>', '', str(p))
    # remove whitespace markers
    clean_text = re.sub(r"[\n\t]", " ", clean_text).strip()
    clean_text = re.sub(' +', ' ', clean_text.strip())
    #print(p)
    doc = nlp(clean_text)
    locations = []
    for j ,ent in enumerate(doc.ents):
        if ent.label_ == "LOC" or ent.label_ == 'GPE':
            start = max(ent.start - 10, 0)
            end = min(ent.end + 10, len(doc))
            context = doc[start:end].text
            ## mapping same loations into one entry
            #if ent.text in novel.locations:
            #  novel.locations[ent.text].contexts.append(context)
            #   novel.locations[ent.text].p_docs.append(doc)
            #else:

            #pickle doc and return path of the pickle file
            #pickle_location =  pickle_doc(novel.file_name, j, ent.text, doc)
            
            #append to novel object
            novel.locations.append(Location(ent.text, ent.label_, context, novel.paragraphs_paths[i]))
            

  #print locations
  print_novel_locations(novel)
  #save csv files
  save_to_csv(novel)
  print("\n")
  


#loop over novels and extract locations
for key, novel_obj in tqdm(novels_dict.items(), desc="Processing Novels", unit="novel_obj"):
  extract_locations(novel_obj)

#for key, novel_obj in novels_dict.items():
    


Processing Novels:   0%|          | 0/100 [00:00<?, ?novel_obj/s]


Analyazing ENG18400_Trollope.xml


Processing Novels:   1%|          | 1/100 [00:27<46:05, 27.93s/novel_obj]

╒═══════════════════════╤═════════════╤═════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════

Processing Novels:   2%|▏         | 2/100 [00:51<41:13, 25.24s/novel_obj]

...

╒════════════════════╤═════════════╤════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════

Processing Novels:  99%|█████████▉| 99/100 [31:20<00:15, 15.75s/novel_obj]

╒═══════════════════════╤═════════════╤═════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════

Processing Novels: 100%|██████████| 100/100 [31:45<00:00, 19.05s/novel_obj]

╒════════════════════╤═════════════╤════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════════

In [ ]:
for key, novel in novels_dict.items():
  print(key, len(novel.locations))


NameError: ignored

In [ ]:

directory = './locations_csv_files'
total_count = 0
gpe_count = 0
for filename in os.listdir(directory):
  filepath = os.path.join(directory, filename)
  df = pd.read_csv(filepath)
  
  total_count+=len(df)

  gpe_count += len(df[df["ent_type"] == 'GPE'])
  print(filename, len(df), len(df[df["ent_type"] == 'GPE']))

print(total_count)
print(gpe_count)

ENG18400_Trollope.xml.csv 206 153
ENG18410_Sinclair.xml.csv 528 237
ENG18411_Tupper.xml.csv 135 103
ENG18440_Disraeli.xml.csv 1011 918
ENG18450_Disraeli.xml.csv 791 743
ENG18460_Reynolds.xml.csv 2209 1948
ENG18470_Aguilar.xml.csv 204 179
ENG18471_Bronte.xml.csv 191 160
ENG18480_Thackeray.xml.csv 1436 1267
ENG18481_Dickens.xml.csv 559 504
ENG18490_Skene.xml.csv 124 30
ENG18510_Kingsley.xml.csv 337 298
ENG18482_Gaskell.xml.csv 277 251
ENG18500_Ainsworth.xml.csv 79 69
ENG18530_Dickens.xml.csv 556 455
ENG18540_Dickens.xml.csv 132 112
ENG18531_Yonge.xml.csv 571 520
ENG18551_Trollope.xml.csv 252 180
ENG18552_Kavanagh.xml.csv 23 22
ENG18560_Yonge.xml.csv 469 415
ENG18570_Bronte.xml.csv 293 269
ENG18600_Clive.xml.csv 39 21
ENG18610_Eliot.xml.csv 80 66
ENG18621_Braddon.xml.csv 463 414
ENG18630_Craik.xml.csv 232 213
ENG18632_Reade.xml.csv 582 525
ENG18641_Stretton.xml.csv 106 91
ENG18650_Trollope.xml.csv 861 806
ENG18640_Blackmore.xml.csv 605 541
ENG18660_Eliot.xml.csv 355 328
ENG18651_Yonge.xml

Updating missing authors, request from Anna

In [ ]:

df= pd.read_csv('./ELTeC-eng-master/ELTeC-eng_metadata.tsv', delimiter='\t')

df.loc[df['filename'] == 'ENG18460_Reynolds', 'author-name'] = 'Reynolds, George'

df[df['filename'] == "ENG18460_Reynolds"]

corpus-id           filename     xmlid       author-name  \
4  ELTeC-eng  ENG18460_Reynolds  ENG18460  Reynolds, George   

                     title  author-birth  author-death author-gender  \
4  The mysteries of London          1814          1879             M   

                        author-ids  reference-year  ...  print-edition  \
4  https://viaf.org/viaf/72764995/            1846  ...            NaN   

  provenance title-ids language  numwords subgenre  narrative-perspective  \
4        NaN       NaN       en    839895      NaN                    NaN   

   size-category  reprint-count time-slot  
4           long            low        T1  

[1 rows x 22 columns]

In [ ]:
df.loc[df['filename'] == 'ENG18641_Stretton', 'author-name'] = 'Stretton, Hesba'

df[df['filename'] == "ENG18641_Stretton"]

corpus-id           filename     xmlid      author-name          title  \
25  ELTeC-eng  ENG18641_Stretton  ENG18641  Stretton, Hesba  Fern's Hollow   

    author-birth  author-death author-gender                       author-ids  \
25          1832          1911             F  https://viaf.org/viaf/29892399/   

    reference-year  ...  print-edition provenance title-ids language  \
25            1864  ...            NaN        NaN       NaN      eng   

    numwords subgenre  narrative-perspective  size-category  reprint-count  \
25     44735      NaN                    NaN          short            low   

   time-slot  
25        T2  

[1 rows x 22 columns]

In [ ]:
df.head()

corpus-id           filename     xmlid              author-name  \
0  ELTeC-eng  ENG18410_Sinclair  ENG18410      Sinclair, Catherine   
1  ELTeC-eng  ENG18440_Disraeli  ENG18440       Disraeli, Benjamin   
2  ELTeC-eng    ENG18411_Tupper  ENG18411  Tupper, Martin Farquhar   
3  ELTeC-eng  ENG18450_Disraeli  ENG18450       Disraeli, Benjamin   
4  ELTeC-eng  ENG18460_Reynolds  ENG18460         Reynolds, George   

                                           title  author-birth  author-death  \
0  Modern Flirtations: or, A Month at Harrowgate          1800          1864   
1              Coningsby: or, The New Generation          1804          1881   
2                    The Twins: A Domestic Novel          1810          1889   
3                      Sybil, Or the Two Nations          1804          1881   
4                        The mysteries of London          1814          1879   

  author-gender                       author-ids  reference-year  ...  \
0             F  https://viaf.org/viaf/37692813/            1841  ...   
1             M  https://viaf.org/viaf/49233448/            1844  ...   
2             M  https://viaf.org/viaf/44385259/            1844  ...   
3             M  https://viaf.org/viaf/49233448/            1845  ...   
4             M  https://viaf.org/viaf/72764995/            1846  ...   

   print-edition                                         provenance title-ids  \
0            NaN                                                NaN       NaN   
1            NaN  Chadwyck-Healey Ltd (A Bell & Howell Informati...       NaN   
2            NaN                                                NaN       NaN   
3            NaN                                                NaN       NaN   
4            NaN                                                NaN       NaN   

  language  numwords subgenre  narrative-perspective  size-category  \
0      eng    188876      NaN                    NaN           long   
1      eng    159046      NaN                    NaN           long   
2      eng     34573      NaN                    NaN          short   
3       en    158160      NaN                    NaN           long   
4       en    839895      NaN                    NaN           long   

   reprint-count time-slot  
0            low        T1  
1            low        T1  
2            low        T1  
3            low        T1  
4            low        T1  

[5 rows x 22 columns]

In [ ]:
df.to_csv("./ELTeC-eng-master/ELTeC-eng_metadata-eidted.tsv", sep='\t', index=False)

In [ ]:
concatenated_df.to_csv("authors_locations_meta_full-amended.tsv", sep='\t', index=False)